In [1]:
!pip3 install OpenNMT-py==1.2.0

Defaulting to user installation because normal site-packages is not writeable


In [2]:
import requests

def get_forms(sysID, lang, lemma_tags_set):
    """lemma_tags_set: `[{"lemma": "go", "tags": "V;PST"}, ...]`"""
    
    request_data = {
        "sysID": sysID,
        "lang": lang,
        "data": lemma_tags_set
    }
    response = requests.post('https://test2.kurdinus.com/oracle/GetForms', json=request_data)
    if response.status_code == 200:
        return response.content.decode()
    else:
        return "#FAILED: " + str(response.status_code)

In [3]:
def check_forms(sysID, lang, lemma_form_tags_set):
    """lemma_forms_tags_set: `[{"lemma": "go", "form": "goed", "tags": "V;PST"}, ...]`"""
    
    request_data = {
        "sysID": sysID,
        "lang": lang,
        "data": lemma_form_tags_set
    }
    response = requests.post('https://test2.kurdinus.com/oracle/CheckForms', json=request_data)
    print(response)
    if response.status_code == 200:
        return response.content.decode()
    else:
        return "#FAILED: " + str(response.status_code)

In [4]:
import pandas as pd
import random

file = pd.read_csv('lat.tsv', sep='\t', header=None).values.tolist()

def get_data(rows, function):
    """rows: `[[lemma, form(if checking data), tags], ...]`
    output: `["lemma\\t form\\t tags", ...]`"""

    lemma_forms_tags_set = []
    for row in rows:
        if row in file: file.remove(row)
        lemma_forms_tags_set.append({"lemma": row[0], "form": row[1], "tags": row[-1]})

    oracle_data = function("fumo_test9", "lat", lemma_forms_tags_set).split('\n')[:-1]
    return oracle_data

In [5]:

rows = random.sample(file, 1000)

# split 90-10 into train and dev
oracle_data = get_data(rows, get_forms)
train_data = oracle_data[:int(len(oracle_data)*0.9)]
dev_data = oracle_data[int(len(oracle_data)*0.9):]
print(oracle_data[:5])

['dehortor\tdehortāberis\tV;IND;ACT;FUT;2;SG', 'adpetissō\tadpetissēminī\tV;IND;PASS;FUT;2;PL', 'alēscō\talēscet\tV;IND;ACT;FUT;3;SG', 'adfor\tadfāris\tV;IND;ACT;PRS;2;SG', 'stinguō\tstinguō\tV;IND;ACT;PRS;1;SG']


In [6]:
def create_data_files(name, data):
    """data: `["lemma\\t form\\t tags", ...]`
    output: `name.src`, `name.tgt` files with the data in this format: `g o # V PST` and `w e n t`"""
    train_src = open(f'data/{name}.src', 'w')
    train_tgt = open(f'data/{name}.tgt', 'w')
    for result in data:
        if type(result) == str: result = result.split('\t')
        if len(result) == 2:
            lemma, tags = result
            word = ''
        else:
            lemma, word, tags = result
        src = ' '.join(list(lemma)) + " # " + ' '.join(tags.split(';'))
        tgt = ' '.join(list(word))
        train_src.write(src + '\n')
        train_tgt.write(tgt + '\n')
    train_src.close()
    train_tgt.close()

In [7]:
create_data_files('train', train_data)
create_data_files('dev', dev_data)

In [8]:
!onmt_preprocess -train_src data/train.src -train_tgt data/train.tgt -valid_src data/dev.src -valid_tgt data/dev.tgt -save_data run/data -overwrite

[2024-05-07 23:06:28,630 INFO] Extracting features...
[2024-05-07 23:06:28,636 INFO]  * number of source features: 0.
[2024-05-07 23:06:28,636 INFO]  * number of target features: 0.
[2024-05-07 23:06:28,636 INFO] Building `Fields` object...
[2024-05-07 23:06:28,636 INFO] Building & saving training data...
[2024-05-07 23:06:28,638 WARNING] Shards for corpus train already exist, will be overwritten because `-overwrite` option is set.
[2024-05-07 23:06:28,656 WARNING] Overwrite shards for corpus None
[2024-05-07 23:06:28,686 INFO] Building shard 0.
[2024-05-07 23:06:28,717 INFO]  * saving 0th train data shard to run/data.train.0.pt.
[2024-05-07 23:06:29,042 INFO]  * tgt vocab size: 35.
[2024-05-07 23:06:29,043 INFO]  * src vocab size: 48.
[2024-05-07 23:06:29,055 INFO] Building & saving validation data...
[2024-05-07 23:06:29,060 WARNING] Shards for corpus valid already exist, will be overwritten because `-overwrite` option is set.
[2024-05-07 23:06:29,066 WARNING] Overwrite shards for co

In [10]:
%%capture cap1 --no-stderr
!onmt_train -data run/data -save_model run/model -encoder_type rnn -rnn_type LSTM -rnn_size 128 -layers 1 -word_vec_size 128 -save_checkpoint_steps 200 -valid_steps 200 -early_stopping 2
with open('train.log', 'w') as f:
    f.write(cap1.stdout)

In [14]:
%%capture cap2 --no-stderr
!onmt_translate -model run/model_step_1000.pt -src data/dev.src -output data/dev.hyp -replace_unk -verbose
with open('pred_scores.log', 'w') as f:
    f.write(cap2.stdout)

In [15]:
!julia evaluate.jl data/dev.tgt data/dev.hyp

Accuracy: 49 / 100   0.49
Character edit distance 2.16
aquābimur -> afuābimur
ēlābimur -> ēlābēmur
tētrinnit -> tētrinniat
galaticantur -> galicantur
ēblandīris -> rēbandieris
perlinīminī -> perliniāminī
adsentiēbāris -> adsentiābāris
quatiēris -> qupiēris
circumstupēmus -> circumstupeāmus
praefābimur -> praefefor
diffīdēbant -> difīdēbant
trānslūcēbunt -> trānscēbunt
perlinīris -> perlinieris
murriēbam -> muriēbam
argūtāris -> argntāris
intermanēbat -> intermantermantermantermantermantermantermantermantermantermantermantermantermantermantermantermante
calumniātur -> calumneris
locētur -> locābitur
corrīdet -> corrīdēt
allābēris -> allābēberis
sardātur -> sardō
mūtāverō -> mūtābō
ruīnātis -> rugnātis
affremētis -> affremitēbitis
impetent -> impetimus
trānsveniēbāmus -> trānsvēbāmus
sardant -> sardō
conmētiar -> conmētiērubor
adtolerant -> adtolent
sāgiō -> sāgiēs
augificor -> augificāruior
hūmēbitis -> hūmenebitis
obsolefīent -> obsolefīī
plēveram -> plēbam
fatīscit -> fatīscet
fit -> 

In [16]:
import re

def get_sorted(text = None):
    if text==None: 
        with open('pred_scores.log', 'r') as file:
            lines = file.readlines()
    else: lines = text.split('\n')

    data = []
    lemma = ''
    tags = ''
    score = 0
    for i in range(len(lines)):
        if lines[i].startswith('SENT'):
            lemma_tags = re.findall(r'\[\'(.*)\'\]', lines[i])[0]
            lemma, tags = lemma_tags.split('#')
            lemma = lemma.replace("'", '').replace(', ', '')
            tags = tags.replace("'", '').replace(', ', ';')[1:]
        elif lines[i].startswith('PRED SCORE'):
            score = float(lines[i].split(':')[1].strip())
        elif lines[i].startswith('PRED'):
            prediction = lines[i].split(':')[1].strip().replace(' ', '')
            data.append((lemma, prediction, tags, score))

    data.sort(key=lambda x: x[3])
    return data

In [17]:
%%capture cap2 --no-stderr
create_data_files("test", file)
!onmt_translate -model run/model_step_1200.pt -src data/test.src -output data/test.hyp -replace_unk -verbose
with open('pred_scores.log', 'w') as f:
    f.write(cap2.stdout)

data = get_sorted()
data = [x[:-1] for x in data]

most_confident = data[-100:]
least_confident = data[:300]
most_confident_results = get_data(most_confident, check_forms)[:-1]
least_confident_results = get_data(least_confident, check_forms)[:-1]

most_confident_incorrect = []
for i, result in enumerate(most_confident_results):
    if result.split('\t')[1] != most_confident[i][1]:
        most_confident_incorrect.append(result)
least_confident_incorrect = []
for i, result in enumerate(least_confident_results):
    if result.split('\t')[1] != least_confident[i][1]:
        least_confident_incorrect.append(result)

incorrect = most_confident_incorrect + least_confident_incorrect
train_data += [x for x in data if x not in most_confident+least_confident]
create_data_files('train', train_data)

!onmt_preprocess -train_src data/train.src -train_tgt data/train.tgt -valid_src data/dev.src -valid_tgt data/dev.tgt -save_data run/data -overwrite
!onmt_train -data run/data -save_model run/model -train_from run/model_step_1200.pt -save_checkpoint_steps 200 -valid_steps 200 -early_stopping 2

In [18]:
%%capture cap2 --no-stderr
create_data_files("test", file)
!onmt_translate -model run/model_step_1200.pt -src data/test.src -output data/test.hyp -replace_unk -verbose
with open('pred_scores.log', 'w') as f:
    f.write(cap2.stdout)

data = get_sorted()
data = [x[:-1] for x in data]

most_confident = data[-100:]
least_confident = data[:300]
most_confident_results = get_data(most_confident, check_forms)[:-1]
least_confident_results = get_data(least_confident, check_forms)[:-1]

most_confident_incorrect = []
for i, result in enumerate(most_confident_results):
    if result.split('\t')[1] != most_confident[i][1]:
        most_confident_incorrect.append(result)
least_confident_incorrect = []
for i, result in enumerate(least_confident_results):
    if result.split('\t')[1] != least_confident[i][1]:
        least_confident_incorrect.append(result)

incorrect = most_confident_incorrect + least_confident_incorrect
train_data += [x for x in data if x not in most_confident+least_confident]
create_data_files('train', train_data)

!onmt_preprocess -train_src data/train.src -train_tgt data/train.tgt -valid_src data/dev.src -valid_tgt data/dev.tgt -save_data run/data -overwrite
!onmt_train -data run/data -save_model run/model -train_from run/model_step_1200.pt -save_checkpoint_steps 200 -valid_steps 200 -early_stopping 2

%%capture cap2 --no-stderr
create_data_files("test", file)
!onmt_translate -model run/model_step_1200.pt -src data/test.src -output data/test.hyp -replace_unk -verbose
with open('pred_scores.log', 'w') as f:
    f.write(cap2.stdout)

data = get_sorted()
data = [x[:-1] for x in data]

most_confident = data[-100:]
least_confident = data[:300]
most_confident_results = get_data(most_confident, check_forms)[:-1]
least_confident_results = get_data(least_confident, check_forms)[:-1]

most_confident_incorrect = []
for i, result in enumerate(most_confident_results):
    if result.split('\t')[1] != most_confident[i][1]:
        most_confident_incorrect.append(result)
least_confident_incorrect = []
for i, result in enumerate(least_confident_results):
    if result.split('\t')[1] != least_confident[i][1]:
        least_confident_incorrect.append(result)

incorrect = most_confident_incorrect + least_confident_incorrect
train_data += [x for x in data if x not in most_confident+least_confident]
create_data_files('train', train_data)

!onmt_preprocess -train_src data/train.src -train_tgt data/train.tgt -valid_src data/dev.src -valid_tgt data/dev.tgt -save_data run/data -overwrite
!onmt_train -data run/data -save_model run/model -train_from run/model_step_1200.pt -save_checkpoint_steps 200 -valid_steps 200 -early_stopping 2

%%capture cap2 --no-stderr
create_data_files("test", file)
!onmt_translate -model run/model_step_1200.pt -src data/test.src -output data/test.hyp -replace_unk -verbose
with open('pred_scores.log', 'w') as f:
    f.write(cap2.stdout)

data = get_sorted()
data = [x[:-1] for x in data]

most_confident = data[-100:]
least_confident = data[:300]
most_confident_results = get_data(most_confident, check_forms)[:-1]
least_confident_results = get_data(least_confident, check_forms)[:-1]

most_confident_incorrect = []
for i, result in enumerate(most_confident_results):
    if result.split('\t')[1] != most_confident[i][1]:
        most_confident_incorrect.append(result)
least_confident_incorrect = []
for i, result in enumerate(least_confident_results):
    if result.split('\t')[1] != least_confident[i][1]:
        least_confident_incorrect.append(result)

incorrect = most_confident_incorrect + least_confident_incorrect
train_data += [x for x in data if x not in most_confident+least_confident]
create_data_files('train', train_data)

!onmt_preprocess -train_src data/train.src -train_tgt data/train.tgt -valid_src data/dev.src -valid_tgt data/dev.tgt -save_data run/data -overwrite
!onmt_train -data run/data -save_model run/model -train_from run/model_step_1200.pt -save_checkpoint_steps 200 -valid_steps 200 -early_stopping 2

In [ ]:
import subprocess
# now predict all data in `file`
# with open('pred_scores.log', 'w') as f:
#     f.write('')

results = []
print(len(file)//100)
for i in range(len(file)//100):
    create_data_files("test", file[100*i : len(file) if 100*(i+1)>len(file) else 100*(i+1)])
    command = "onmt_translate -model run/model_step_1200.pt -src data/test.src -output data/test.hyp -replace_unk -verbose"
    process = subprocess.run(command, shell=True)
    data = process.stdout
    data = [x[:-1] for x in get_sorted(data)]
    # print(data[:10])
    results += get_data(data, check_forms)


218


/home/bitmap4/.local/lib/python3.10/site-packages/torch/nn/modules/rnn.py:83: UserWarning: dropout option adds dropout after all but last recurrent layer, so non-zero dropout expects num_layers greater than 1, but got dropout=0.3 and num_layers=1
  warnings.warn("dropout option adds dropout after all but last "
[2024-05-07 22:40:01,735 INFO] Translating shard 0.
/home/bitmap4/.local/lib/python3.10/site-packages/onmt/translate/beam_search.py:209: UserWarning: An output with one or more elements was resized since it had shape [150], which does not match the required output shape [30, 5]. This behavior is deprecated, and in a future PyTorch release outputs will not be resized unless they have zero elements. You can explicitly reuse an out tensor t by resizing it, inplace, to zero elements with t.resize_(0). (Triggered internally at ../aten/src/ATen/native/Resize.cpp:28.)
  torch.mul(self.topk_scores, length_penalty, out=self.topk_log_probs)
[2024-05-07 22:40:01,796 INFO] 
SENT 1: ['i', 'm

<Response [200]>


/home/bitmap4/.local/lib/python3.10/site-packages/torch/nn/modules/rnn.py:83: UserWarning: dropout option adds dropout after all but last recurrent layer, so non-zero dropout expects num_layers greater than 1, but got dropout=0.3 and num_layers=1
  warnings.warn("dropout option adds dropout after all but last "
[2024-05-07 22:40:04,821 INFO] Translating shard 0.
/home/bitmap4/.local/lib/python3.10/site-packages/onmt/translate/beam_search.py:209: UserWarning: An output with one or more elements was resized since it had shape [150], which does not match the required output shape [30, 5]. This behavior is deprecated, and in a future PyTorch release outputs will not be resized unless they have zero elements. You can explicitly reuse an out tensor t by resizing it, inplace, to zero elements with t.resize_(0). (Triggered internally at ../aten/src/ATen/native/Resize.cpp:28.)
  torch.mul(self.topk_scores, length_penalty, out=self.topk_log_probs)
[2024-05-07 22:40:04,937 INFO] 
SENT 1: ['s', 'e

<Response [200]>


...

<Response [200]>


/home/bitmap4/.local/lib/python3.10/site-packages/torch/nn/modules/rnn.py:83: UserWarning: dropout option adds dropout after all but last recurrent layer, so non-zero dropout expects num_layers greater than 1, but got dropout=0.3 and num_layers=1
  warnings.warn("dropout option adds dropout after all but last "
[2024-05-07 22:53:06,476 INFO] Translating shard 0.
/home/bitmap4/.local/lib/python3.10/site-packages/onmt/translate/beam_search.py:209: UserWarning: An output with one or more elements was resized since it had shape [150], which does not match the required output shape [30, 5]. This behavior is deprecated, and in a future PyTorch release outputs will not be resized unless they have zero elements. You can explicitly reuse an out tensor t by resizing it, inplace, to zero elements with t.resize_(0). (Triggered internally at ../aten/src/ATen/native/Resize.cpp:28.)
  torch.mul(self.topk_scores, length_penalty, out=self.topk_log_probs)
[2024-05-07 22:53:06,576 INFO] 
SENT 1: ['d', 'ē

<Response [200]>


/home/bitmap4/.local/lib/python3.10/site-packages/torch/nn/modules/rnn.py:83: UserWarning: dropout option adds dropout after all but last recurrent layer, so non-zero dropout expects num_layers greater than 1, but got dropout=0.3 and num_layers=1
  warnings.warn("dropout option adds dropout after all but last "
[2024-05-07 22:53:10,489 INFO] Translating shard 0.
/home/bitmap4/.local/lib/python3.10/site-packages/onmt/translate/beam_search.py:209: UserWarning: An output with one or more elements was resized since it had shape [150], which does not match the required output shape [30, 5]. This behavior is deprecated, and in a future PyTorch release outputs will not be resized unless they have zero elements. You can explicitly reuse an out tensor t by resizing it, inplace, to zero elements with t.resize_(0). (Triggered internally at ../aten/src/ATen/native/Resize.cpp:28.)
  torch.mul(self.topk_scores, length_penalty, out=self.topk_log_probs)
[2024-05-07 22:53:10,542 INFO] 
SENT 1: ['s', 'u

<Response [200]>


In [ ]:
with open('predictions', 'w') as f:
    for row in results:
        f.write(row + '\n')

21800